In [1]:
import math
import torch
import pickle
import torch.cuda
import torchvision.transforms as transforms
import torch.utils.data as data
import torchvision.datasets as dsets
import os
from utils.BBBConvmodel import BBBAlexNet, BBBLeNet, BBB3Conv3FC, BBBVGG16
from utils.BBBlayers import GaussianVariationalInference
import numpy as np
from scipy.stats import norm
cuda = torch.cuda.is_available()
import pandas as pd
from matplotlib import pyplot as plt
import scipy

In [2]:
batch_size = 32
lr = 0.001
dataset = 'MNIST'
network = 'lenet'
if dataset == 'MNIST':
    model = torch.load("../results/{}_withbias_b{}_lr{}_{}.pth".format(network, batch_size, lr, dataset))
elif dataset == 'CIFAR-10':
    model = BBBLeNet(outputs=10, inputs=3)
    model_name = 'lenet5'
    num_epochs = 50
    model.load_state_dict(torch.load('../model_with_bias/model{}_param_epoch{}_lr{}_bs{}.pkl'.format(model_name,num_epochs,lr,batch_size), map_location='cpu'))
net = BBBLeNet
num_samples = 10
beta_type = "Blundell"

In [3]:
# dimensions of input and output
if dataset == 'MNIST':    # train with MNIST
    outputs = 10
    inputs = 1
elif dataset == 'CIFAR-10':  # train with CIFAR-10
    outputs = 10
    inputs = 3
elif dataset == 'CIFAR-100':    # train with CIFAR-100
    outputs = 100
    inputs = 3

if net == BBBLeNet or BBB3Conv3FC:
    resize = 32
elif net == BBBAlexNet:
    resize = 227

In [4]:
'''
LOADING DATASET
'''

if dataset == 'MNIST':
    transform = transforms.Compose([transforms.Resize((resize, resize)), transforms.ToTensor(),
                                    transforms.Normalize((0.1307,), (0.3081,))])
    train_dataset = dsets.MNIST(root="data", download=True, transform=transform)
    val_dataset = dsets.MNIST(root="data", download=True, train=False, transform=transform)

elif dataset == 'CIFAR-100':
    transform = transforms.Compose([transforms.Resize((resize, resize)), transforms.ToTensor(),
                                    transforms.Normalize((0.485, 0.456, 0.406), (0.229, 0.224, 0.225))])
    train_dataset = dsets.CIFAR100(root="data", download=True, transform=transform)
    val_dataset = dsets.CIFAR100(root='data', download=True, train=False, transform=transform)

elif dataset == 'CIFAR-10':
    transform = transforms.Compose([transforms.Resize((resize, resize)), transforms.ToTensor(),
                                    transforms.Normalize((0.485, 0.456, 0.406), (0.229, 0.224, 0.225))])
    train_dataset = dsets.CIFAR10(root="data", download=True, transform=transform)
    val_dataset = dsets.CIFAR10(root='data', download=True, train=False, transform=transform)

In [5]:
loader_val = data.DataLoader(dataset=val_dataset, batch_size=batch_size, shuffle=False)

In [6]:
model.state_dict().keys()

odict_keys(['conv1.qw_mean', 'conv1.qw_logvar', 'conv1.qb_mean', 'conv1.qb_logvar', 'conv1.conv_qw_mean', 'conv1.conv_qw_si', 'conv1.log_alpha', 'conv2.qw_mean', 'conv2.qw_logvar', 'conv2.qb_mean', 'conv2.qb_logvar', 'conv2.conv_qw_mean', 'conv2.conv_qw_si', 'conv2.log_alpha', 'fc1.qw_mean', 'fc1.qw_logvar', 'fc1.qb_mean', 'fc1.qb_logvar', 'fc1.fc_qw_mean', 'fc1.fc_qw_si', 'fc1.log_alpha', 'fc2.qw_mean', 'fc2.qw_logvar', 'fc2.qb_mean', 'fc2.qb_logvar', 'fc2.fc_qw_mean', 'fc2.fc_qw_si', 'fc2.log_alpha', 'fc3.qw_mean', 'fc3.qw_logvar', 'fc3.qb_mean', 'fc3.qb_logvar', 'fc3.fc_qw_mean', 'fc3.fc_qw_si', 'fc3.log_alpha', 'layers.0.qw_mean', 'layers.0.qw_logvar', 'layers.0.qb_mean', 'layers.0.qb_logvar', 'layers.0.conv_qw_mean', 'layers.0.conv_qw_si', 'layers.0.log_alpha', 'layers.3.qw_mean', 'layers.3.qw_logvar', 'layers.3.qb_mean', 'layers.3.qb_logvar', 'layers.3.conv_qw_mean', 'layers.3.conv_qw_si', 'layers.3.log_alpha', 'layers.7.qw_mean', 'layers.7.qw_logvar', 'layers.7.qb_mean', 'layers

# 合并weights

In [7]:
if network == "lenet":
    w_name = ['layers.0.qw_', 'layers.3.qw_', 'layers.7.qw_','layers.9.qw_', 'layers.11.qw_']
    b_name = ['layers.0.qb_', 'layers.3.qb_', 'layers.7.qb_','layers.9.qb_', 'layers.11.qb_']
elif network == "vgg16":
    w_name = ['layers.0.qw_', 'layers.2.qw_', 'layers.4.qw_','layers.6.qw_', 'layers.8.qw_', 
              'layers.10.qw_', 'layers.12.qw_', 'layers.14.qw_', 'layers.16.qw_', 'layers.18.qw_',
            'layers.20.qw_', 'layers.22.qw_', 'layers.24.qw_', 'layers.27.qw_', 'layers.30.qw_', 'layers.33.qw_']
    b_name = ['layers.0.qb_', 'layers.2.qb_', 'layers.4.qb_','layers.6.qb_', 'layers.8.qb_', 
              'layers.10.qb_', 'layers.12.qb_', 'layers.14.qb_', 'layers.16.qb_', 'layers.18.qb_',
            'layers.20.qb_', 'layers.22.qb_', 'layers.24.qb_', 'layers.27.qb_', 'layers.30.qb_', 'layers.33.qb_']

In [8]:
model = model.cpu()

In [9]:
whole_w = []
for (i, j) in zip(w_name, b_name):
    whole_w.append(model.state_dict()['{}mean'.format(i)].numpy().ravel())
    whole_w.append(model.state_dict()['{}mean'.format(j)].numpy().ravel())
whole_w = np.concatenate(whole_w)

In [10]:
len(whole_w)

61706

In [11]:
len(whole_w[np.abs(whole_w) <= 1e-2])

41342

# 神经网络精度计算函数

In [12]:
vi = GaussianVariationalInference(torch.nn.CrossEntropyLoss())

def run_epoch(loader, epoch, is_training=False, model=model):
    m = math.ceil(len(loader.dataset) / loader.batch_size)

    accuracies = []
    likelihoods = []
    kls = []
    losses = []

    for i, (images, labels) in enumerate(loader):
        # # Repeat samples (Casper's trick)
        # x = images.view(-1, inputs, resize, resize).repeat(num_samples, 1, 1, 1)
        # y = labels.repeat(num_samples)
        x = images.view(-1, inputs, resize, resize)
        y = labels
        if cuda:
            x = x.cuda()
            y = y.cuda()

        if beta_type == "Blundell":
            beta = 2 ** (m - (i + 1)) / (2 ** m - 1)
        elif beta_type == "Soenderby":
            beta = min(epoch / (num_epochs//4), 1)
        elif beta_type == "Standard":
            beta = 1 / m
        else:
            beta = 0

        logits, kl = model.probforward(x)
        loss = vi(logits, y, kl, beta)
        ll = -loss.data.mean() + beta*kl.data.mean()

        if is_training:
            optimiser.zero_grad()
            loss.backward()
            optimiser.step()

        _, predicted = logits.max(1)
        accuracy = (predicted.data.cpu() == y.cpu()).float().mean()

        accuracies.append(accuracy)
        losses.append(loss.data.mean())
        kls.append(beta*kl.data.mean())
        likelihoods.append(ll)

    diagnostics = {'loss': sum(losses)/len(losses),
                   'acc': sum(accuracies)/len(accuracies),
                   'kl': sum(kls)/len(kls),
                   'likelihood': sum(likelihoods)/len(likelihoods)}

    return diagnostics

In [13]:
model = model.cuda()
diagnostics_val = run_epoch(loader_val, epoch=1)

logits tensor([[ -8.6153,  -6.3100,  -4.6404,  -8.4938,  -3.9079,  -9.0428,  -9.4296,
           8.7852,  -7.8256,  -4.1476],
        [ -4.4386,  -3.7873,  10.8983,  -5.4856, -11.6047,  -8.5518,  -4.5211,
          -4.2620,  -3.2508, -10.1334],
        [ -6.6087,   6.7665,  -3.1530,  -9.5303,  -3.2520,  -6.4991,  -5.8468,
          -3.8064,  -2.9020,  -5.6285],
        [  7.0597,  -2.4644,  -5.4185,  -6.1355,  -7.4552,  -6.1931,  -2.2529,
          -4.6394,  -3.6700,  -1.6050],
        [ -5.0723,  -4.2454,  -5.7879,  -8.3565,   5.2612,  -6.0432,  -4.6800,
          -5.8512,  -5.3866,   1.7893],
        [ -7.2173,   9.0046,  -4.6937, -10.4146,  -4.4675, -10.0514,  -5.3328,
          -3.2398,  -2.4154,  -6.2947],
        [ -6.3261,  -2.4710,  -5.1840,  -9.5782,   6.2672,  -5.8999,  -4.0993,
          -4.4997,  -2.4691,  -0.7000],
        [ -6.0927,  -5.0355,  -6.5105,  -4.5345,  -0.5045,  -5.7918,  -8.6658,
          -6.5069,  -1.8389,   6.7191],
        [ -7.3169,  -6.3782,  -8.8335,  -

In [14]:
diagnostics_val

{'loss': tensor(117.0525, device='cuda:0'),
 'acc': tensor(0.9887),
 'kl': tensor(117.0158, device='cuda:0'),
 'likelihood': tensor(-0.0367, device='cuda:0')}

In [15]:
model2 = BBBLeNet(outputs, inputs)

In [16]:
tmp = model.state_dict()

In [22]:
for name in tmp.keys():
    if 'logvar' in name:
        tmp[name] = -1e-6 * torch.ones_like(tmp[name])
    if 'si' in name:
        tmp[name] = torch.zeros_like(tmp[name])
    if 'log_alpha' in name:
        tmp[name] = -1e-6 * torch.ones_like(tmp[name])

In [23]:
model2.load_state_dict(tmp)

<All keys matched successfully>

In [24]:
model2 = model2.cuda()

In [25]:
diagnostics_val = run_epoch(loader_val, epoch=1, model=model2)

logits tensor([[-1.0284e+01, -7.4894e+00,  6.0146e+00, -6.3799e+00, -1.6435e+01,
         -6.3051e+00, -8.4740e+00, -2.3450e-01, -5.8959e+00, -5.6491e+00],
        [-1.4708e+01, -8.8863e+00,  8.4914e+00, -2.8758e+00, -4.8346e+00,
         -8.9885e+00, -3.8427e+00, -1.1864e+01, -5.2596e+00, -1.0116e+01],
        [-4.3615e+00, -6.3727e+00, -4.9292e+00, -8.1744e+00, -5.6775e-01,
         -2.7028e+00, -9.2001e+00,  9.0942e-01, -1.0065e+00, -2.6665e+00],
        [ 5.0220e+00, -5.6407e+00, -5.7547e+00, -3.2640e+00, -9.5341e+00,
         -9.9702e-03, -1.2974e-01,  7.1089e-01, -2.2440e+00, -1.6199e+00],
        [-1.2976e+01, -1.1746e+01, -2.9928e+00, -5.5866e+00, -6.7920e+00,
          1.6106e+00, -8.2789e-01, -7.7970e-01, -3.5868e+00, -3.1893e+00],
        [-1.2678e+01,  1.1736e+01, -5.6474e+00, -2.9877e+01, -9.8718e+00,
         -2.1420e+00, -6.6054e+00, -1.8650e+01, -3.1255e+00, -1.2242e+01],
        [-7.6554e+00, -3.9778e+00, -4.3260e+00, -5.8604e+00, -5.6444e+00,
         -2.6154e+00, -3.

In [26]:
diagnostics_val

{'loss': tensor(1579.7454, device='cuda:0'),
 'acc': tensor(0.5954),
 'kl': tensor(1576.8530, device='cuda:0'),
 'likelihood': tensor(-2.8928, device='cuda:0')}

In [15]:
def evaluate(loader, epoch=1):
    m = math.ceil(len(loader.dataset) / loader.batch_size)

    accuracies = []

    for i, (images, labels) in enumerate(loader):
        # # Repeat samples (Casper's trick)
        # x = images.view(-1, inputs, resize, resize).repeat(num_samples, 1, 1, 1)
        # y = labels.repeat(num_samples)

        x = images.view(-1, inputs, resize, resize)
        y = labels

        if cuda:
            x = x.cuda()
            y = y.cuda()

        logits = cpr_model(x)
        _, predicted = torch.max(logits.data, 1)
        accuracy = (predicted.data.cpu() == y.cpu()).float().mean()

        accuracies.append(accuracy)

    diagnostics = {'acc': sum(accuracies)/len(accuracies)}

    return diagnostics

把BNN的weights套进确定性网络，测试精度

In [18]:
uncompressed_list = []
for (i, j) in zip(w_name, b_name):
    # w
    vecs_u1 = model.state_dict()['{}mean'.format(i)]
    uncompressed_list.append(vecs_u1)
    # b
    vecs_u2 = np.zeros_like(model.state_dict()['{}mean'.format(j)])
    uncompressed_list.append(vecs_u2)

if network == "lenet":
    # lenet
    from model import lenet
    cpr_model=lenet(inputs)
elif network == "vgg16":
    from model import VGG16
    cpr_model = VGG16(inputs)
name_uncpr=cpr_model.state_dict().keys()
uncpr_state_dict = dict(zip(name_uncpr, uncompressed_list))
cpr_model.load_state_dict(uncpr_state_dict)
# 用压缩后的模型计算loss，acc等
cpr_model = cpr_model.cuda()
diagnostics_uncpr_val = evaluate(loader_val)

TypeError: can't convert cuda:0 device type tensor to numpy. Use Tensor.cpu() to copy the tensor to host memory first.

In [17]:
diagnostics_uncpr_val

{'acc': tensor(0.0967)}

# all layers放在一起压缩

In [56]:
def compress_coordinates(means, stds, beta, bitlengths):
    # N = len(means.ravel()) = len(stds.ravel())
    # C = len(codepoints)
    optima = np.empty_like(means)
    optima_lengths = np.empty_like(means, dtype=int)
    for i in range(0, 10000000, 100000):
        if i % 100000 == 0:
            print(i / 1000000)
        squared_errors = (codepoints[np.newaxis, :] - means.ravel()[i:i+100000, np.newaxis])**2
            # shape (N, C)
        weighted_penalties = (2 * beta) * stds.ravel()[i:i+100000, np.newaxis]**2 * bitlengths[np.newaxis, :]
            # shape (N, C)
        optima_idxs = np.argmin(squared_errors + weighted_penalties, axis=1)
        optima.ravel()[i:i+100000] = codepoints[optima_idxs]
        optima_lengths.ravel()[i:i+100000] = bitlengths[optima_idxs]
    return optima, optima_lengths

In [57]:
model = model.cpu()

In [58]:
results = [['full', 'full', diagnostics_val['acc'].numpy(), 'None']]
compressed_len_list = []
betas = [0.0001, 0.001, 0.01, 0.1, 1, 10, 100]
bitlengths = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10]
# betas = [0.01]
# bitlengths = [2]

empirical_mean = np.mean(whole_w)
empirical_std = np.std(whole_w)

for max_codepoint_length in bitlengths:
    for beta_ in betas:
        compressed_len = 0
        compressed_list = []
        for (i, j) in zip(w_name, b_name):
            codepoints_and_lengths = [
                (scipy.stats.norm.ppf(codepoint_xi, loc=empirical_mean, scale=empirical_std), length)
                for length in range(max_codepoint_length+1)
                for codepoint_xi in np.arange(0.5**(length+1), 1, 0.5**length)
            ]
            codepoints = np.array([codepoint for codepoint, _ in codepoints_and_lengths])
            lengths = np.array([length for _, length in codepoints_and_lengths])
            # compress w
            vecs_u1 = model.state_dict()['{}mean'.format(i)].numpy()
            stds_u1 = np.exp(model.state_dict()['{}logvar'.format(i)].numpy())
            compressed1, cpr_len1 = compress_coordinates(vecs_u1,stds_u1,beta_,lengths)
            compressed1 = torch.from_numpy(compressed1)
            compressed_list.append(compressed1)
            compressed_len += np.sum(cpr_len1)
            # compress b
            vecs_u2 = model.state_dict()['{}mean'.format(j)].numpy()
            stds_u2 = np.exp(model.state_dict()['{}logvar'.format(j)].numpy())
            compressed2, cpr_len2 = compress_coordinates(vecs_u2,stds_u2,beta_,lengths)
            compressed2 = torch.from_numpy(compressed2)
            compressed_list.append(compressed2)
            compressed_len += np.sum(cpr_len2)

        compressed_len_list.append([max_codepoint_length, beta_, compressed_len, 'global'])
        
        if network == "lenet":
            # lenet
            from model import lenet
            cpr_model=lenet(inputs)
        elif network == "vgg16":
            from model import VGG16
            cpr_model = VGG16(inputs)
        print(max_codepoint_length, beta_)
        name_cpr=cpr_model.state_dict().keys()
        cpr_state_dict = dict(zip(name_cpr, compressed_list))
        cpr_model.load_state_dict(cpr_state_dict)
        # 用压缩后的模型计算loss，acc等
        cpr_model = cpr_model.cuda()
        diagnostics_cpr_val = evaluate(loader_val)
        results.append([max_codepoint_length, beta_, diagnostics_cpr_val['acc'].numpy(), 'global'])

0.0
0.1
0.2
0.3
0.4
0.5
0.6
0.7
0.8
0.9
1.0
1.1
1.2
1.3
1.4
1.5
1.6
1.7
1.8
1.9
2.0
2.1
2.2
2.3
2.4
2.5
2.6
2.7
2.8
2.9
3.0
3.1
3.2
3.3
3.4
3.5
3.6
3.7
3.8
3.9
4.0
4.1
4.2
4.3
4.4
4.5
4.6
4.7
4.8
4.9
5.0
5.1
5.2
5.3
5.4
5.5
5.6
5.7
5.8
5.9
6.0
6.1
6.2
6.3
6.4
6.5
6.6
6.7
6.8
6.9
7.0
7.1
7.2
7.3
7.4
7.5
7.6
7.7
7.8
7.9
8.0
8.1
8.2
8.3
8.4
8.5
8.6
8.7
8.8
8.9
9.0
9.1
9.2
9.3
9.4
9.5
9.6
9.7
9.8
9.9
0.0
0.1
0.2
0.3
0.4
0.5
0.6
0.7
0.8
0.9
1.0
1.1
1.2
1.3
1.4
1.5
1.6
1.7
1.8
1.9
2.0
2.1
2.2
2.3
2.4
2.5
2.6
2.7
2.8
2.9
3.0
3.1
3.2
3.3
3.4
3.5
3.6
3.7
3.8
3.9
4.0
4.1
4.2
4.3
4.4
4.5
4.6
4.7
4.8
4.9
5.0
5.1
5.2
5.3
5.4
5.5
5.6
5.7
5.8
5.9
6.0
6.1
6.2
6.3
6.4
6.5
6.6
6.7
6.8
6.9
7.0
7.1
7.2
7.3
7.4
7.5
7.6
7.7
7.8
7.9
8.0
8.1
8.2
8.3
8.4
8.5
8.6
8.7
8.8
8.9
9.0
9.1
9.2
9.3
9.4
9.5
9.6
9.7
9.8
9.9
0.0
0.1
0.2
0.3
0.4
0.5
0.6
0.7
0.8
0.9
1.0
1.1
1.2
1.3
1.4
1.5
1.6
1.7
1.8
1.9
2.0
2.1
2.2
2.3
2.4
2.5
2.6
2.7
2.8
2.9
3.0
3.1
3.2
3.3
3.4
3.5
3.6
3.7
3.8
3.9
4.0
4.1
4.2
4.3
4.4
4.5
4.6
4.7
4.8
4.9


# 每层用不同P(z)

In [59]:
for max_codepoint_length in bitlengths:
    for beta_ in betas:
        compressed_len = 0
        compressed_list = []
        for (i, j) in zip(w_name, b_name):
            # w
            vecs_u1 = model.state_dict()['{}mean'.format(i)].numpy()
            stds_u1 = np.exp(model.state_dict()['{}logvar'.format(i)].numpy())
            # b
            vecs_u2 = model.state_dict()['{}mean'.format(j)].numpy()
            stds_u2 = np.exp(model.state_dict()['{}logvar'.format(j)].numpy())
            # 先把w和b合并在一起再拟合高斯
            vecs_u = np.concatenate([vecs_u1.ravel(), vecs_u2.ravel()])

            empirical_mean = np.mean(vecs_u)
            empirical_std = np.std(vecs_u)
            codepoints_and_lengths = [
                (scipy.stats.norm.ppf(codepoint_xi, loc=empirical_mean, scale=empirical_std), length)
                for length in range(max_codepoint_length+1)
                for codepoint_xi in np.arange(0.5**(length+1), 1, 0.5**length)
            ]
            codepoints = np.array([codepoint for codepoint, _ in codepoints_and_lengths])
            lengths = np.array([length for _, length in codepoints_and_lengths])

            compressed1, cpr_len1 = compress_coordinates(vecs_u1,stds_u1,beta_,lengths)
            compressed1 = torch.from_numpy(compressed1)
            compressed_list.append(compressed1)
            compressed_len += np.sum(cpr_len1)
            # compress b
            compressed2, cpr_len2 = compress_coordinates(vecs_u2,stds_u2,beta_,lengths)
            compressed2 = torch.from_numpy(compressed2)
            compressed_list.append(compressed2)
            compressed_len += np.sum(cpr_len2)

        compressed_len_list.append([max_codepoint_length, beta_, compressed_len, 'layer-wise'])
        # lenet
        from model import lenet_b
        cpr_model=lenet_b(inputs)
        print(max_codepoint_length, beta_)
        print(compressed_list)
        name_cpr=cpr_model.state_dict().keys()
        cpr_state_dict = dict(zip(name_cpr, compressed_list))
        cpr_model.load_state_dict(cpr_state_dict)
        cpr_model = cpr_model.cuda()
        # 用压缩后的模型计算loss，acc等
        diagnostics_cpr_val = evaluate(loader_val)
        results.append([max_codepoint_length, beta_, diagnostics_cpr_val['acc'].numpy(), 'layer-wise'])

0.0
0.1
0.2
0.3
0.4
0.5
0.6
0.7
0.8
0.9
1.0
1.1
1.2
1.3
1.4
1.5
1.6
1.7
1.8
1.9
2.0
2.1
2.2
2.3
2.4
2.5
2.6
2.7
2.8
2.9
3.0
3.1
3.2
3.3
3.4
3.5
3.6
3.7
3.8
3.9
4.0
4.1
4.2
4.3
4.4
4.5
4.6
4.7
4.8
4.9
5.0
5.1
5.2
5.3
5.4
5.5
5.6
5.7
5.8
5.9
6.0
6.1
6.2
6.3
6.4
6.5
6.6
6.7
6.8
6.9
7.0
7.1
7.2
7.3
7.4
7.5
7.6
7.7
7.8
7.9
8.0
8.1
8.2
8.3
8.4
8.5
8.6
8.7
8.8
8.9
9.0
9.1
9.2
9.3
9.4
9.5
9.6
9.7
9.8
9.9
0.0
0.1
0.2
0.3
0.4
0.5
0.6
0.7
0.8
0.9
1.0
1.1
1.2
1.3
1.4
1.5
1.6
1.7
1.8
1.9
2.0
2.1
2.2
2.3
2.4
2.5
2.6
2.7
2.8
2.9
3.0
3.1
3.2
3.3
3.4
3.5
3.6
3.7
3.8
3.9
4.0
4.1
4.2
4.3
4.4
4.5
4.6
4.7
4.8
4.9
5.0
5.1
5.2
5.3
5.4
5.5
5.6
5.7
5.8
5.9
6.0
6.1
6.2
6.3
6.4
6.5
6.6
6.7
6.8
6.9
7.0
7.1
7.2
7.3
7.4
7.5
7.6
7.7
7.8
7.9
8.0
8.1
8.2
8.3
8.4
8.5
8.6
8.7
8.8
8.9
9.0
9.1
9.2
9.3
9.4
9.5
9.6
9.7
9.8
9.9
0.0
0.1
0.2
0.3
0.4
0.5
0.6
0.7
0.8
0.9
1.0
1.1
1.2
1.3
1.4
1.5
1.6
1.7
1.8
1.9
2.0
2.1
2.2
2.3
2.4
2.5
2.6
2.7
2.8
2.9
3.0
3.1
3.2
3.3
3.4
3.5
3.6
3.7
3.8
3.9
4.0
4.1
4.2
4.3
4.4
4.5
4.6
4.7
4.8
4.9


In [60]:
results = pd.DataFrame(results)
results.columns = ['bitlength', 'beta', 'acc_test', 'method']

In [61]:
results

bitlength    beta    acc_test      method
0        full    full  0.60902554        None
1           1  0.0001  0.15355432      global
2           1   0.001  0.15355432      global
3           1    0.01  0.15345447      global
4           1     0.1  0.15365416      global
..        ...     ...         ...         ...
136        10    0.01    0.548722  layer-wise
137        10     0.1     0.55002  layer-wise
138        10       1  0.54852235  layer-wise
139        10      10  0.52146566  layer-wise
140        10     100  0.18909745  layer-wise

[141 rows x 4 columns]

In [62]:
results.to_csv("./results/lenet_withbias_b{}_lr{}_{}_gaussian.csv".format(batch_size, lr, dataset), index=False)

In [63]:
cpr_len_df = pd.DataFrame(compressed_len_list)
cpr_len_df.columns = ['bitlength', 'beta', 'len', 'method']
cpr_len_df['len'] = cpr_len_df['len'] / whole_w.size

In [64]:
cpr_len_df

bitlength      beta       len      method
0            1    0.0001  0.656920      global
1            1    0.0010  0.656904      global
2            1    0.0100  0.656872      global
3            1    0.1000  0.656582      global
4            1    1.0000  0.652888      global
..         ...       ...       ...         ...
135         10    0.0100  5.246912  layer-wise
136         10    0.1000  3.694336  layer-wise
137         10    1.0000  2.295197  layer-wise
138         10   10.0000  1.339177  layer-wise
139         10  100.0000  0.541738  layer-wise

[140 rows x 4 columns]

In [65]:
cpr_len_df.to_csv("./results/bits_lenet_withbias_b{}_lr{}_{}_gaussian.csv".format(batch_size, lr, dataset), index=False)